# DNN Speech Enhancement Tutorial

In the jupyter notebook, we will use pytorch to implement a simple DNN that used for speech enhancement.

## 1. Import package
First, we will import all packages we need for this project: 

In [1]:
import librosa
import ffmpeg
import os
import torch
import torch.nn.functional as Func
import torch.nn as nn
import numpy as np
from torch.autograd import Variable
import torch.optim as optim
import torch.utils.data as data
from torch.nn.utils.rnn import pack_padded_sequence
from torch.nn.utils.rnn import pad_packed_sequence
import copy


## 2. Preprocessing and Build Dataloader

### a) Training Dataloader
The input X for the DNN is the padded magnitude of STFT of a noisy signal.
The input M for the DNN is the padded magnitude of STFT of a clean signal.

In the following sections, we first paired each noisy speech with clean speech by filename and save their padded magnitude of STFT data in .npy format for Training data. 

In [2]:
#Data Path for training data
#Noisy Speech
trainPath = './Data/wav/noisy/Train/'
trainMixedList = os.listdir(trainPath)
trainLength = len(trainMixedList)

#Clean Speech
cleanPath = './Data/wav/clean/Train/'
cleanSpeechList = os.listdir(cleanPath)
cleanSpeechLength = len(cleanSpeechList)

#.npy output folder
#trainPyPath = './Data/npy/Train/'
trainPyPath = './Data/npy/Train_frame/'

In [3]:
c = 0
for index in range (0,trainLength): #For each noisy speech
    xFile = trainMixedList[index]
    #print(xFile)
    a = xFile.split('_',2) #get filename
    #print(a[-1])
    for j in range(0,cleanSpeechLength):
        #Try to match the filename of noisy and clean speech
        if a[-1] == cleanSpeechList[j]:
            
            #load the time domain data for clean speech
            ss,sr = librosa.load(cleanPath + cleanSpeechList[j],sr=None)
            
            #Padded the time domain signal by 0s in order to make all the signals same length. 
            #124621 is the length for the longest signal in Training data.
            #ss = np.pad(ss, (0,124621-ss.shape[0]), 'constant', constant_values=0)
            
            #calculate STFT and its magnitude
            S = librosa.stft(ss,n_fft=512,hop_length=160,win_length=400)
            S = np.abs(S)
            
    #Similar to clean speech, load the time domain data for noisy speech, pad the data and calculate STFT         
    sx,sr = librosa.load(trainPath + xFile,sr=None)
    #sx = np.pad(sx, (0,124621-sx.shape[0]), 'constant', constant_values=0)
    
    X = librosa.stft(sx,n_fft=512,hop_length=160,win_length=400)
    X = np.abs(X)
    
    #for each frame
    for j in range(S.shape[1]):
        
        print(c)
        #Save the data of clean and noisy speech in .npy format
        Xfile = trainPyPath + 'x' + str(c) +'.npy'
        Mfile = trainPyPath + 'm' + str(c) +'.npy'
        #X is the magnitude STFT for noisy speech, M is the magnitude STFT for clean speech
        np.save(Xfile,X[:,j])
        np.save(Mfile,S[:,j])
        c+=1
        print(index, trainLength)

0
0 1044
1
0 1044
2
0 1044
3
0 1044
4
0 1044
5
0 1044
6
0 1044
7
0 1044
8
0 1044
9
0 1044
10
0 1044
11
0 1044
12
0 1044
13
0 1044
14
0 1044
15
0 1044
16
0 1044
17
0 1044
18
0 1044
19
0 1044
20
0 1044
21
0 1044
22
0 1044
23
0 1044
24
0 1044
25
0 1044
26
0 1044
27
0 1044
28
0 1044
29
0 1044
30
0 1044
31
0 1044
32
0 1044
33
0 1044
34
0 1044
35
0 1044
36
0 1044
37
0 1044
38
0 1044
39
0 1044
40
0 1044
41
0 1044
42
0 1044
43
0 1044
44
0 1044
45
0 1044
46
0 1044
47
0 1044
48
0 1044
49
0 1044
50
0 1044
51
0 1044
52
0 1044
53
0 1044
54
0 1044
55
0 1044
56
0 1044
57
0 1044
58
0 1044
59
0 1044
60
0 1044
61
0 1044
62
0 1044
63
0 1044
64
0 1044
65
0 1044
66
0 1044
67
0 1044
68
0 1044
69
0 1044
70
0 1044
71
0 1044
72
0 1044
73
0 1044
74
0 1044
75
0 1044
76
0 1044
77
0 1044
78
0 1044
79
0 1044
80
0 1044
81
0 1044
82
0 1044
83
0 1044
84
0 1044
85
0 1044
86
0 1044
87
0 1044
88
0 1044
89
0 1044
90
0 1044
91
0 1044
92
0 1044
93
0 1044
94
0 1044
95
0 1044
96
0 1044
97
0 1044
98
0 1044
99
0 1044
100
0 1044

4 1044
887
4 1044
888
4 1044
889
4 1044
890
4 1044
891
4 1044
892
4 1044
893
4 1044
894
4 1044
895
4 1044
896
4 1044
897
4 1044
898
4 1044
899
4 1044
900
4 1044
901
4 1044
902
4 1044
903
4 1044
904
4 1044
905
4 1044
906
4 1044
907
4 1044
908
4 1044
909
4 1044
910
4 1044
911
4 1044
912
4 1044
913
4 1044
914
4 1044
915
4 1044
916
4 1044
917
4 1044
918
4 1044
919
4 1044
920
4 1044
921
4 1044
922
4 1044
923
4 1044
924
4 1044
925
4 1044
926
4 1044
927
4 1044
928
4 1044
929
4 1044
930
4 1044
931
4 1044
932
4 1044
933
4 1044
934
4 1044
935
4 1044
936
4 1044
937
4 1044
938
4 1044
939
4 1044
940
4 1044
941
4 1044
942
4 1044
943
4 1044
944
4 1044
945
4 1044
946
4 1044
947
4 1044
948
4 1044
949
4 1044
950
4 1044
951
4 1044
952
4 1044
953
4 1044
954
4 1044
955
4 1044
956
4 1044
957
4 1044
958
4 1044
959
4 1044
960
4 1044
961
4 1044
962
4 1044
963
4 1044
964
4 1044
965
4 1044
966
4 1044
967
4 1044
968
4 1044
969
4 1044
970
4 1044
971
4 1044
972
4 1044
973
4 1044
974
4 1044
975
4 1044
976
4 1044
977

8 1044
1662
8 1044
1663
8 1044
1664
8 1044
1665
8 1044
1666
8 1044
1667
8 1044
1668
8 1044
1669
8 1044
1670
8 1044
1671
8 1044
1672
8 1044
1673
8 1044
1674
8 1044
1675
8 1044
1676
8 1044
1677
8 1044
1678
8 1044
1679
8 1044
1680
8 1044
1681
8 1044
1682
8 1044
1683
8 1044
1684
8 1044
1685
8 1044
1686
8 1044
1687
8 1044
1688
8 1044
1689
8 1044
1690
8 1044
1691
8 1044
1692
8 1044
1693
8 1044
1694
8 1044
1695
8 1044
1696
8 1044
1697
8 1044
1698
8 1044
1699
8 1044
1700
8 1044
1701
8 1044
1702
8 1044
1703
8 1044
1704
8 1044
1705
8 1044
1706
8 1044
1707
8 1044
1708
8 1044
1709
8 1044
1710
8 1044
1711
8 1044
1712
8 1044
1713
8 1044
1714
8 1044
1715
8 1044
1716
8 1044
1717
8 1044
1718
8 1044
1719
8 1044
1720
8 1044
1721
8 1044
1722
8 1044
1723
8 1044
1724
8 1044
1725
8 1044
1726
8 1044
1727
8 1044
1728
8 1044
1729
8 1044
1730
8 1044
1731
8 1044
1732
8 1044
1733
8 1044
1734
8 1044
1735
8 1044
1736
8 1044
1737
8 1044
1738
8 1044
1739
8 1044
1740
8 1044
1741
8 1044
1742
8 1044
1743
8 1044
1744
8 10

12 1044
2410
12 1044
2411
12 1044
2412
12 1044
2413
12 1044
2414
12 1044
2415
12 1044
2416
12 1044
2417
12 1044
2418
12 1044
2419
12 1044
2420
12 1044
2421
12 1044
2422
12 1044
2423
12 1044
2424
12 1044
2425
12 1044
2426
12 1044
2427
12 1044
2428
12 1044
2429
12 1044
2430
12 1044
2431
12 1044
2432
12 1044
2433
12 1044
2434
12 1044
2435
12 1044
2436
12 1044
2437
12 1044
2438
12 1044
2439
12 1044
2440
12 1044
2441
12 1044
2442
12 1044
2443
12 1044
2444
12 1044
2445
12 1044
2446
12 1044
2447
12 1044
2448
12 1044
2449
12 1044
2450
12 1044
2451
12 1044
2452
12 1044
2453
12 1044
2454
12 1044
2455
12 1044
2456
12 1044
2457
12 1044
2458
12 1044
2459
12 1044
2460
12 1044
2461
12 1044
2462
12 1044
2463
12 1044
2464
12 1044
2465
12 1044
2466
12 1044
2467
12 1044
2468
12 1044
2469
12 1044
2470
12 1044
2471
12 1044
2472
12 1044
2473
12 1044
2474
12 1044
2475
12 1044
2476
12 1044
2477
12 1044
2478
12 1044
2479
12 1044
2480
12 1044
2481
12 1044
2482
12 1044
2483
12 1044
2484
12 1044
2485
12 1044
2486

15 1044
3196
15 1044
3197
15 1044
3198
15 1044
3199
15 1044
3200
15 1044
3201
15 1044
3202
15 1044
3203
15 1044
3204
15 1044
3205
15 1044
3206
15 1044
3207
15 1044
3208
15 1044
3209
15 1044
3210
15 1044
3211
15 1044
3212
15 1044
3213
15 1044
3214
15 1044
3215
15 1044
3216
15 1044
3217
16 1044
3218
16 1044
3219
16 1044
3220
16 1044
3221
16 1044
3222
16 1044
3223
16 1044
3224
16 1044
3225
16 1044
3226
16 1044
3227
16 1044
3228
16 1044
3229
16 1044
3230
16 1044
3231
16 1044
3232
16 1044
3233
16 1044
3234
16 1044
3235
16 1044
3236
16 1044
3237
16 1044
3238
16 1044
3239
16 1044
3240
16 1044
3241
16 1044
3242
16 1044
3243
16 1044
3244
16 1044
3245
16 1044
3246
16 1044
3247
16 1044
3248
16 1044
3249
16 1044
3250
16 1044
3251
16 1044
3252
16 1044
3253
16 1044
3254
16 1044
3255
16 1044
3256
16 1044
3257
16 1044
3258
16 1044
3259
16 1044
3260
16 1044
3261
16 1044
3262
16 1044
3263
16 1044
3264
16 1044
3265
16 1044
3266
16 1044
3267
16 1044
3268
16 1044
3269
16 1044
3270
16 1044
3271
16 1044
3272

...

1030 1044
197402
1030 1044
197403
1030 1044
197404
1030 1044
197405
1030 1044
197406
1030 1044
197407
1030 1044
197408
1030 1044
197409
1030 1044
197410
1030 1044
197411
1030 1044
197412
1030 1044
197413
1030 1044
197414
1030 1044
197415
1030 1044
197416
1030 1044
197417
1030 1044
197418
1031 1044
197419
1031 1044
197420
1031 1044
197421
1031 1044
197422
1031 1044
197423
1031 1044
197424
1031 1044
197425
1031 1044
197426
1031 1044
197427
1031 1044
197428
1031 1044
197429
1031 1044
197430
1031 1044
197431
1031 1044
197432
1031 1044
197433
1031 1044
197434
1031 1044
197435
1031 1044
197436
1031 1044
197437
1031 1044
197438
1031 1044
197439
1031 1044
197440
1031 1044
197441
1031 1044
197442
1031 1044
197443
1031 1044
197444
1031 1044
197445
1031 1044
197446
1031 1044
197447
1031 1044
197448
1031 1044
197449
1031 1044
197450
1031 1044
197451
1031 1044
197452
1031 1044
197453
1031 1044
197454
1031 1044
197455
1031 1044
197456
1031 1044
197457
1031 1044
197458
1031 1044
197459
1031 1044
1974

1033 1044
197945
1033 1044
197946
1033 1044
197947
1033 1044
197948
1033 1044
197949
1033 1044
197950
1033 1044
197951
1033 1044
197952
1033 1044
197953
1033 1044
197954
1033 1044
197955
1033 1044
197956
1033 1044
197957
1033 1044
197958
1033 1044
197959
1033 1044
197960
1033 1044
197961
1033 1044
197962
1033 1044
197963
1033 1044
197964
1033 1044
197965
1033 1044
197966
1033 1044
197967
1033 1044
197968
1033 1044
197969
1033 1044
197970
1033 1044
197971
1033 1044
197972
1033 1044
197973
1033 1044
197974
1033 1044
197975
1033 1044
197976
1034 1044
197977
1034 1044
197978
1034 1044
197979
1034 1044
197980
1034 1044
197981
1034 1044
197982
1034 1044
197983
1034 1044
197984
1034 1044
197985
1034 1044
197986
1034 1044
197987
1034 1044
197988
1034 1044
197989
1034 1044
197990
1034 1044
197991
1034 1044
197992
1034 1044
197993
1034 1044
197994
1034 1044
197995
1034 1044
197996
1034 1044
197997
1034 1044
197998
1034 1044
197999
1034 1044
198000
1034 1044
198001
1034 1044
198002
1034 1044
1980

1037 1044
198556
1037 1044
198557
1037 1044
198558
1037 1044
198559
1037 1044
198560
1037 1044
198561
1037 1044
198562
1037 1044
198563
1037 1044
198564
1037 1044
198565
1037 1044
198566
1037 1044
198567
1037 1044
198568
1037 1044
198569
1037 1044
198570
1037 1044
198571
1037 1044
198572
1037 1044
198573
1037 1044
198574
1037 1044
198575
1037 1044
198576
1037 1044
198577
1037 1044
198578
1037 1044
198579
1037 1044
198580
1037 1044
198581
1037 1044
198582
1037 1044
198583
1037 1044
198584
1037 1044
198585
1037 1044
198586
1037 1044
198587
1037 1044
198588
1037 1044
198589
1037 1044
198590
1037 1044
198591
1037 1044
198592
1037 1044
198593
1037 1044
198594
1037 1044
198595
1037 1044
198596
1037 1044
198597
1037 1044
198598
1037 1044
198599
1037 1044
198600
1037 1044
198601
1037 1044
198602
1037 1044
198603
1037 1044
198604
1037 1044
198605
1037 1044
198606
1037 1044
198607
1037 1044
198608
1037 1044
198609
1037 1044
198610
1037 1044
198611
1037 1044
198612
1037 1044
198613
1037 1044
1986

1039 1044
199079
1039 1044
199080
1039 1044
199081
1039 1044
199082
1039 1044
199083
1039 1044
199084
1039 1044
199085
1039 1044
199086
1039 1044
199087
1039 1044
199088
1039 1044
199089
1039 1044
199090
1039 1044
199091
1039 1044
199092
1039 1044
199093
1039 1044
199094
1039 1044
199095
1039 1044
199096
1039 1044
199097
1039 1044
199098
1039 1044
199099
1039 1044
199100
1039 1044
199101
1039 1044
199102
1039 1044
199103
1039 1044
199104
1039 1044
199105
1039 1044
199106
1039 1044
199107
1039 1044
199108
1039 1044
199109
1039 1044
199110
1039 1044
199111
1039 1044
199112
1039 1044
199113
1039 1044
199114
1039 1044
199115
1039 1044
199116
1039 1044
199117
1039 1044
199118
1039 1044
199119
1039 1044
199120
1039 1044
199121
1039 1044
199122
1039 1044
199123
1039 1044
199124
1039 1044
199125
1039 1044
199126
1039 1044
199127
1039 1044
199128
1039 1044
199129
1039 1044
199130
1039 1044
199131
1039 1044
199132
1039 1044
199133
1039 1044
199134
1039 1044
199135
1039 1044
199136
1039 1044
1991

1042 1044
199716
1042 1044
199717
1042 1044
199718
1042 1044
199719
1042 1044
199720
1042 1044
199721
1042 1044
199722
1042 1044
199723
1042 1044
199724
1042 1044
199725
1042 1044
199726
1042 1044
199727
1042 1044
199728
1042 1044
199729
1042 1044
199730
1042 1044
199731
1042 1044
199732
1042 1044
199733
1042 1044
199734
1042 1044
199735
1042 1044
199736
1042 1044
199737
1042 1044
199738
1042 1044
199739
1042 1044
199740
1042 1044
199741
1042 1044
199742
1042 1044
199743
1042 1044
199744
1042 1044
199745
1042 1044
199746
1042 1044
199747
1042 1044
199748
1043 1044
199749
1043 1044
199750
1043 1044
199751
1043 1044
199752
1043 1044
199753
1043 1044
199754
1043 1044
199755
1043 1044
199756
1043 1044
199757
1043 1044
199758
1043 1044
199759
1043 1044
199760
1043 1044
199761
1043 1044
199762
1043 1044
199763
1043 1044
199764
1043 1044
199765
1043 1044
199766
1043 1044
199767
1043 1044
199768
1043 1044
199769
1043 1044
199770
1043 1044
199771
1043 1044
199772
1043 1044
199773
1043 1044
1997

In [4]:
#Dataloader for traning data
class trainDataLoader(data.Dataset):
    def __init__(self):
        #self.dataPath = './Data/npy/Train/'
        self.dataPath = './Data/npy/Train_frame/'
    def __getitem__(self, index):
        xFile = self.dataPath + 'x' + str(index) + '.npy'
        mFile = self.dataPath + 'm' + str(index) + '.npy'
        X = np.load(xFile)
        M_truth = np.load(mFile)
        return torch.from_numpy(X),torch.from_numpy(M_truth)
    def __len__(self):
        #Number of files
        return 199919
    

### b) Validation Dataloader

Similar to Training Data loader, we will then build the validation Dataloader

In [5]:
validPath = './Data/wav/noisy/Valid/'
validMixedList = os.listdir(validPath)
validLength = len(validMixedList)

cleanPath = './Data/wav/clean/Valid/'
cleanSpeechList = os.listdir(cleanPath)
cleanSpeechLength = len(cleanSpeechList)

#validPyPath = './Data/npy/Valid/'
validPyPath = './Data/npy/Valid_frame/'

In [6]:
c = 0
#for index in range (0,10):
for index in range (0,validLength):
    xFile = validMixedList[index]
    a = xFile.split('_',2)
    for j in range(0,cleanSpeechLength):
        #print(j)
        if a[-1] == cleanSpeechList[j]:
            #print(cleanSpeechList[j])
            ss,sr = librosa.load(cleanPath + cleanSpeechList[j],sr=None)
            #ss = np.pad(ss, (0,118989-ss.shape[0]), 'constant', constant_values=0)
            
            S = librosa.stft(ss,n_fft=512,hop_length=160,win_length=400)
            #print(S)
            S = np.abs(S)
    #print(sx.shape[0])
    sx,sr = librosa.load(validPath + xFile,sr=None)
    #sx = np.pad(sx, (0,118989-sx.shape[0]), 'constant', constant_values=0)
    
    X = librosa.stft(sx,n_fft=512,hop_length=160,win_length=400)
    X = np.abs(X)
    
    #for each frame
    for j in range(S.shape[1]):
        
        print(c)
        #Save the data of clean and noisy speech in .npy format
        Xfile = validPyPath + 'x' + str(c) +'.npy'
        Mfile = validPyPath + 'm' + str(c) +'.npy'
        #X is the magnitude STFT for noisy speech, M is the magnitude STFT for clean speech
        np.save(Xfile,X[:,j])
        np.save(Mfile,S[:,j])
        c+=1
        print(index, validLength)

0
0 228
1
0 228
2
0 228
3
0 228
4
0 228
5
0 228
6
0 228
7
0 228
8
0 228
9
0 228
10
0 228
11
0 228
12
0 228
13
0 228
14
0 228
15
0 228
16
0 228
17
0 228
18
0 228
19
0 228
20
0 228
21
0 228
22
0 228
23
0 228
24
0 228
25
0 228
26
0 228
27
0 228
28
0 228
29
0 228
30
0 228
31
0 228
32
0 228
33
0 228
34
0 228
35
0 228
36
0 228
37
0 228
38
0 228
39
0 228
40
0 228
41
0 228
42
0 228
43
0 228
44
0 228
45
0 228
46
0 228
47
0 228
48
0 228
49
0 228
50
0 228
51
0 228
52
0 228
53
0 228
54
0 228
55
0 228
56
0 228
57
0 228
58
0 228
59
0 228
60
0 228
61
0 228
62
0 228
63
0 228
64
0 228
65
0 228
66
0 228
67
0 228
68
0 228
69
0 228
70
0 228
71
0 228
72
0 228
73
0 228
74
0 228
75
0 228
76
0 228
77
0 228
78
0 228
79
0 228
80
0 228
81
0 228
82
0 228
83
0 228
84
0 228
85
0 228
86
0 228
87
0 228
88
0 228
89
0 228
90
0 228
91
0 228
92
0 228
93
0 228
94
0 228
95
0 228
96
0 228
97
0 228
98
0 228
99
0 228
100
0 228
101
0 228
102
0 228
103
0 228
104
0 228
105
0 228
106
0 228
107
0 228
108
0 228
109
0 228
110
0 228


4 228
902
4 228
903
4 228
904
4 228
905
4 228
906
4 228
907
4 228
908
4 228
909
4 228
910
4 228
911
4 228
912
4 228
913
4 228
914
4 228
915
4 228
916
4 228
917
4 228
918
4 228
919
4 228
920
4 228
921
4 228
922
4 228
923
4 228
924
4 228
925
4 228
926
4 228
927
4 228
928
4 228
929
4 228
930
4 228
931
4 228
932
4 228
933
4 228
934
5 228
935
5 228
936
5 228
937
5 228
938
5 228
939
5 228
940
5 228
941
5 228
942
5 228
943
5 228
944
5 228
945
5 228
946
5 228
947
5 228
948
5 228
949
5 228
950
5 228
951
5 228
952
5 228
953
5 228
954
5 228
955
5 228
956
5 228
957
5 228
958
5 228
959
5 228
960
5 228
961
5 228
962
5 228
963
5 228
964
5 228
965
5 228
966
5 228
967
5 228
968
5 228
969
5 228
970
5 228
971
5 228
972
5 228
973
5 228
974
5 228
975
5 228
976
5 228
977
5 228
978
5 228
979
5 228
980
5 228
981
5 228
982
5 228
983
5 228
984
5 228
985
5 228
986
5 228
987
5 228
988
5 228
989
5 228
990
5 228
991
5 228
992
5 228
993
5 228
994
5 228
995
5 228
996
5 228
997
5 228
998
5 228
999
5 228
1000
5 228
100

9 228
1734
9 228
1735
9 228
1736
9 228
1737
9 228
1738
9 228
1739
9 228
1740
9 228
1741
9 228
1742
9 228
1743
9 228
1744
9 228
1745
9 228
1746
9 228
1747
9 228
1748
9 228
1749
9 228
1750
9 228
1751
9 228
1752
9 228
1753
9 228
1754
9 228
1755
9 228
1756
9 228
1757
9 228
1758
9 228
1759
9 228
1760
9 228
1761
9 228
1762
9 228
1763
9 228
1764
9 228
1765
9 228
1766
9 228
1767
9 228
1768
9 228
1769
9 228
1770
9 228
1771
9 228
1772
9 228
1773
9 228
1774
9 228
1775
9 228
1776
9 228
1777
9 228
1778
9 228
1779
9 228
1780
9 228
1781
9 228
1782
9 228
1783
9 228
1784
9 228
1785
9 228
1786
9 228
1787
9 228
1788
9 228
1789
9 228
1790
9 228
1791
9 228
1792
9 228
1793
9 228
1794
9 228
1795
9 228
1796
9 228
1797
9 228
1798
9 228
1799
9 228
1800
9 228
1801
9 228
1802
9 228
1803
9 228
1804
9 228
1805
10 228
1806
10 228
1807
10 228
1808
10 228
1809
10 228
1810
10 228
1811
10 228
1812
10 228
1813
10 228
1814
10 228
1815
10 228
1816
10 228
1817
10 228
1818
10 228
1819
10 228
1820
10 228
1821
10 228
1822
10 2

13 228
2566
13 228
2567
13 228
2568
13 228
2569
13 228
2570
13 228
2571
13 228
2572
13 228
2573
13 228
2574
13 228
2575
13 228
2576
13 228
2577
13 228
2578
13 228
2579
13 228
2580
13 228
2581
13 228
2582
13 228
2583
13 228
2584
13 228
2585
13 228
2586
13 228
2587
13 228
2588
13 228
2589
13 228
2590
13 228
2591
13 228
2592
13 228
2593
13 228
2594
13 228
2595
13 228
2596
13 228
2597
13 228
2598
13 228
2599
13 228
2600
13 228
2601
13 228
2602
13 228
2603
13 228
2604
13 228
2605
13 228
2606
13 228
2607
13 228
2608
13 228
2609
13 228
2610
13 228
2611
13 228
2612
13 228
2613
13 228
2614
13 228
2615
13 228
2616
13 228
2617
13 228
2618
13 228
2619
13 228
2620
13 228
2621
13 228
2622
13 228
2623
13 228
2624
13 228
2625
13 228
2626
13 228
2627
13 228
2628
13 228
2629
13 228
2630
13 228
2631
13 228
2632
13 228
2633
13 228
2634
13 228
2635
13 228
2636
13 228
2637
13 228
2638
13 228
2639
13 228
2640
13 228
2641
13 228
2642
13 228
2643
13 228
2644
13 228
2645
13 228
2646
13 228
2647
13 228
2648
13 2

17 228
3391
17 228
3392
17 228
3393
17 228
3394
17 228
3395
17 228
3396
17 228
3397
17 228
3398
17 228
3399
17 228
3400
17 228
3401
17 228
3402
17 228
3403
17 228
3404
17 228
3405
17 228
3406
17 228
3407
17 228
3408
17 228
3409
18 228
3410
18 228
3411
18 228
3412
18 228
3413
18 228
3414
18 228
3415
18 228
3416
18 228
3417
18 228
3418
18 228
3419
18 228
3420
18 228
3421
18 228
3422
18 228
3423
18 228
3424
18 228
3425
18 228
3426
18 228
3427
18 228
3428
18 228
3429
18 228
3430
18 228
3431
18 228
3432
18 228
3433
18 228
3434
18 228
3435
18 228
3436
18 228
3437
18 228
3438
18 228
3439
18 228
3440
18 228
3441
18 228
3442
18 228
3443
18 228
3444
18 228
3445
18 228
3446
18 228
3447
18 228
3448
18 228
3449
18 228
3450
18 228
3451
18 228
3452
18 228
3453
18 228
3454
18 228
3455
18 228
3456
18 228
3457
18 228
3458
18 228
3459
18 228
3460
18 228
3461
18 228
3462
18 228
3463
18 228
3464
18 228
3465
18 228
3466
18 228
3467
18 228
3468
18 228
3469
18 228
3470
18 228
3471
18 228
3472
18 228
3473
18 2

...

211 228
39952
211 228
39953
211 228
39954
211 228
39955
211 228
39956
211 228
39957
211 228
39958
211 228
39959
211 228
39960
211 228
39961
211 228
39962
211 228
39963
211 228
39964
211 228
39965
211 228
39966
211 228
39967
211 228
39968
211 228
39969
211 228
39970
211 228
39971
211 228
39972
211 228
39973
211 228
39974
211 228
39975
211 228
39976
211 228
39977
211 228
39978
211 228
39979
211 228
39980
211 228
39981
211 228
39982
211 228
39983
211 228
39984
211 228
39985
211 228
39986
211 228
39987
211 228
39988
211 228
39989
211 228
39990
211 228
39991
211 228
39992
211 228
39993
211 228
39994
211 228
39995
211 228
39996
211 228
39997
211 228
39998
211 228
39999
211 228
40000
211 228
40001
211 228
40002
211 228
40003
211 228
40004
211 228
40005
211 228
40006
211 228
40007
211 228
40008
211 228
40009
211 228
40010
211 228
40011
211 228
40012
211 228
40013
211 228
40014
211 228
40015
211 228
40016
211 228
40017
211 228
40018
211 228
40019
211 228
40020
211 228
40021
211 228
40022
211 22

215 228
40704
215 228
40705
215 228
40706
215 228
40707
215 228
40708
215 228
40709
215 228
40710
215 228
40711
215 228
40712
215 228
40713
215 228
40714
215 228
40715
215 228
40716
215 228
40717
215 228
40718
215 228
40719
215 228
40720
215 228
40721
215 228
40722
215 228
40723
215 228
40724
215 228
40725
215 228
40726
215 228
40727
215 228
40728
215 228
40729
215 228
40730
215 228
40731
215 228
40732
215 228
40733
215 228
40734
215 228
40735
215 228
40736
215 228
40737
215 228
40738
215 228
40739
215 228
40740
215 228
40741
215 228
40742
215 228
40743
215 228
40744
215 228
40745
215 228
40746
215 228
40747
215 228
40748
215 228
40749
215 228
40750
215 228
40751
215 228
40752
215 228
40753
215 228
40754
215 228
40755
215 228
40756
215 228
40757
215 228
40758
215 228
40759
215 228
40760
215 228
40761
215 228
40762
215 228
40763
215 228
40764
215 228
40765
215 228
40766
215 228
40767
215 228
40768
215 228
40769
215 228
40770
215 228
40771
215 228
40772
215 228
40773
215 228
40774
215 22

218 228
41345
218 228
41346
218 228
41347
218 228
41348
218 228
41349
218 228
41350
218 228
41351
218 228
41352
218 228
41353
218 228
41354
218 228
41355
218 228
41356
218 228
41357
218 228
41358
218 228
41359
218 228
41360
218 228
41361
218 228
41362
218 228
41363
218 228
41364
218 228
41365
218 228
41366
218 228
41367
218 228
41368
218 228
41369
218 228
41370
218 228
41371
218 228
41372
218 228
41373
218 228
41374
218 228
41375
218 228
41376
218 228
41377
218 228
41378
218 228
41379
218 228
41380
218 228
41381
218 228
41382
218 228
41383
218 228
41384
218 228
41385
218 228
41386
218 228
41387
218 228
41388
218 228
41389
218 228
41390
218 228
41391
218 228
41392
218 228
41393
218 228
41394
218 228
41395
218 228
41396
218 228
41397
218 228
41398
218 228
41399
218 228
41400
218 228
41401
218 228
41402
218 228
41403
218 228
41404
218 228
41405
218 228
41406
218 228
41407
218 228
41408
218 228
41409
218 228
41410
218 228
41411
218 228
41412
218 228
41413
218 228
41414
218 228
41415
218 22

222 228
42087
222 228
42088
222 228
42089
222 228
42090
222 228
42091
222 228
42092
222 228
42093
222 228
42094
222 228
42095
222 228
42096
222 228
42097
222 228
42098
222 228
42099
222 228
42100
222 228
42101
222 228
42102
222 228
42103
222 228
42104
222 228
42105
222 228
42106
222 228
42107
222 228
42108
222 228
42109
222 228
42110
222 228
42111
222 228
42112
222 228
42113
222 228
42114
222 228
42115
222 228
42116
222 228
42117
222 228
42118
222 228
42119
222 228
42120
222 228
42121
222 228
42122
222 228
42123
222 228
42124
222 228
42125
222 228
42126
222 228
42127
222 228
42128
222 228
42129
222 228
42130
222 228
42131
222 228
42132
222 228
42133
222 228
42134
222 228
42135
222 228
42136
222 228
42137
222 228
42138
222 228
42139
222 228
42140
222 228
42141
222 228
42142
222 228
42143
222 228
42144
222 228
42145
222 228
42146
222 228
42147
222 228
42148
222 228
42149
222 228
42150
222 228
42151
222 228
42152
222 228
42153
222 228
42154
222 228
42155
222 228
42156
222 228
42157
222 22

226 228
42745
226 228
42746
226 228
42747
226 228
42748
226 228
42749
226 228
42750
226 228
42751
226 228
42752
226 228
42753
226 228
42754
226 228
42755
226 228
42756
226 228
42757
226 228
42758
226 228
42759
226 228
42760
226 228
42761
226 228
42762
226 228
42763
226 228
42764
226 228
42765
226 228
42766
226 228
42767
226 228
42768
226 228
42769
226 228
42770
226 228
42771
226 228
42772
226 228
42773
226 228
42774
226 228
42775
226 228
42776
226 228
42777
226 228
42778
226 228
42779
226 228
42780
226 228
42781
226 228
42782
226 228
42783
226 228
42784
226 228
42785
226 228
42786
226 228
42787
226 228
42788
226 228
42789
226 228
42790
226 228
42791
226 228
42792
226 228
42793
226 228
42794
226 228
42795
226 228
42796
226 228
42797
226 228
42798
226 228
42799
226 228
42800
226 228
42801
226 228
42802
226 228
42803
226 228
42804
226 228
42805
226 228
42806
226 228
42807
226 228
42808
226 228
42809
226 228
42810
226 228
42811
226 228
42812
226 228
42813
226 228
42814
226 228
42815
226 22

In [7]:
class valDataLoader(data.Dataset):
    def __init__(self):
        #self.dataPath = './Data/npy/Valid/'
        self.dataPath = './Data/npy/Valid_frame/'
    def __getitem__(self, index):
        xFile = self.dataPath + 'x' + str(index) + '.npy'
        mFile = self.dataPath + 'm' + str(index) + '.npy'
        X = np.load(xFile)
        M_truth = np.load(mFile)
        return torch.from_numpy(X),torch.from_numpy(M_truth)
    def __len__(self):
        #Number of files
        return 43116

### c) Testing Dataloader

The last one the Testing Dataloader. Unlike Training and Validation, we don't need clean speech data for Testing. Therefore, we only store the .npy data for noisy speeches.

In [8]:
testPath = './Data/wav/noisy/Test/'
testMixedList = os.listdir(testPath)
testLength = len(testMixedList)
testPyPath ='./Data/npy/Test/'
#testPyPath ='./Data/npy/Test_frame/'
teList = os.listdir(testPyPath)

In [16]:
for index in range(0, testLength):
#for index in range(0, 10):
    xFile = testMixedList[index]
    sx, sr = librosa.load(testPath + xFile, sr=None)
    X = librosa.stft(sx,n_fft=512,hop_length=160,win_length=400)
    X = np.abs(X)
    a = xFile.split('.',1)
    Xfile = testPyPath + a[0] + '.npy'
    np.save(Xfile, X)
    print(index,testLength)

0 228
1 228
2 228
3 228
4 228
5 228
6 228
7 228
8 228
9 228
10 228
11 228
12 228
13 228
14 228
15 228
16 228
17 228
18 228
19 228
20 228
21 228
22 228
23 228
24 228
25 228
26 228
27 228
28 228
29 228
30 228
31 228
32 228
33 228
34 228
35 228
36 228
37 228
38 228
39 228
40 228
41 228
42 228
43 228
44 228
45 228
46 228
47 228
48 228
49 228
50 228
51 228
52 228
53 228
54 228
55 228
56 228
57 228
58 228
59 228
60 228
61 228
62 228
63 228
64 228
65 228
66 228
67 228
68 228
69 228
70 228
71 228
72 228
73 228
74 228
75 228
76 228
77 228
78 228
79 228
80 228
81 228
82 228
83 228
84 228
85 228
86 228
87 228
88 228
89 228
90 228
91 228
92 228
93 228
94 228
95 228
96 228
97 228
98 228
99 228
100 228
101 228
102 228
103 228
104 228
105 228
106 228
107 228
108 228
109 228
110 228
111 228
112 228
113 228
114 228
115 228
116 228
117 228
118 228
119 228
120 228
121 228
122 228
123 228
124 228
125 228
126 228
127 228
128 228
129 228
130 228
131 228
132 228
133 228
134 228
135 228
136 228
137 228
138 22

In [9]:
class testDataLoader(data.Dataset):
    def __init__(self):
        self.dataPath = './Data/npy/Test/'
        self.dataList = teList
    def __getitem__(self, index):
        xFile = self.dataPath + self.dataList[index]
        X = np.load(xFile)
        return torch.from_numpy(X).t()
    def __len__(self):
        #Number of files
        return 228

## Model

### Model Structure
Next, we will start to construct our model. In this tutorial, we only use a simple 4-layer DNN. 

The input data has a dimension of n * 257 which n is the time stamps and 257 is the number of frequency bins.
The dimension of hidden layers and output layer is describe as following. Each layer will be followed by a RELU activation layer.

In [10]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()

        self.fc1 = nn.Linear(257,1024)
        self.fc2 = nn.Linear(1024,1024)
        self.fc3 = nn.Linear(1024,1024)
        self.fc4 = nn.Linear(1024,257)
        
    def forward(self,audio):
        audio = Func.relu(self.fc1(audio))
        audio = Func.relu(self.fc2(audio))
        audio = Func.relu(self.fc3(audio))
        audio = self.fc4(audio)
        return audio
        

### Initialize weights

We initialize our weight by using the pre-defined function from pytorch which give us a normal distributed weights.

Detained explaination can be found in: https://pytorch.org/docs/stable/nn.init.html

In [11]:
def weights(m):
    if isinstance(m,nn.Linear):
        nn.init.xavier_normal(m.weight.data)
        nn.init.constant(m.bias.data,0.1)

## Train
### Initialization
The following lines intialize our model and weights. It also defines our Loss function and optimizer

In [12]:
model = Net()
model.apply(weights)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters())


/home/liu477/.local/lib/python3.5/site-packages/ipykernel_launcher.py:3: UserWarning: nn.init.xavier_normal is now deprecated in favor of nn.init.xavier_normal_.
  This is separate from the ipykernel package so we can avoid doing imports until
/home/liu477/.local/lib/python3.5/site-packages/ipykernel_launcher.py:4: UserWarning: nn.init.constant is now deprecated in favor of nn.init.constant_.
  after removing the cwd from sys.path.


### GPU or CPU

You need to use CUDA if you want to use your GPU for training. 

Detailed about cuda can be found in:https://docs.nvidia.com/cuda/index.html

In [13]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.cuda()
model = model.to(device)
criterion.cuda()

MSELoss()

### Initialize Dataloader
Initialize the Dataloder we define previously. Set the parameters such as batch size and shuffle.

Documentation can be find here: https://pytorch.org/docs/stable/data.html


In [24]:
trainData = data.DataLoader(trainDataLoader(),batch_size = 10000,shuffle=True,drop_last = True) 
valData = data.DataLoader(valDataLoader(),batch_size = 10000,shuffle=True,drop_last = True) 

### Traning Process
The big for loop for your training. Use everything defined preiously, set number of epoches and train your model.

In [25]:
num_epochs = 20
best_model = copy.deepcopy(model.state_dict())
best_loss = 9999

for epoch in range(num_epochs):
    print('Epoch {}/{}'.format(epoch, num_epochs - 1))
    loss = 0.0 
    vali_loss = 0.0
    for step, (audio, target) in enumerate(trainData): 
        audio = audio.to(device)
        target = target.to(device)
        model.train()
        output = model(audio)
        newLoss = criterion(output,target)
        loss += newLoss.data
        #print(step,loss)
        optimizer.zero_grad()
        newLoss.backward()
        optimizer.step()
        print("Train step:"+str(step)+"/"+str(len(trainData)))
    for step, (audio, target) in enumerate(valData): 
        audio = audio.to(device)
        target = target.to(device)        
        model.eval()
        output = model(audio)
        new_valiLoss = criterion(output,target)
        vali_loss += new_valiLoss.data
        #print(step,vali_loss)
        if vali_loss < best_loss:
                best_loss = vali_loss
                best_model = copy.deepcopy(model.state_dict())
        print("Valid step:"+str(step)+"/"+str(len(valData)))
    print('Epoch:{:2},Loss:{:>.5f}'.format(epoch,loss))
    print('Epoch:{:2},Loss:{:>.5f}'.format(epoch,vali_loss)) 

Epoch 0/19
Train step:0/19
Train step:1/19
Train step:2/19
Train step:3/19
Train step:4/19
Train step:5/19
Train step:6/19
Train step:7/19
Train step:8/19
Train step:9/19
Train step:10/19
Train step:11/19
Train step:12/19
Train step:13/19
Train step:14/19
Train step:15/19
Train step:16/19
Train step:17/19
Train step:18/19
Valid step:0/4
Valid step:1/4
Valid step:2/4
Valid step:3/4
Epoch: 0,Loss:1.98215
Epoch: 0,Loss:0.41902
Epoch 1/19
Train step:0/19
Train step:1/19
Train step:2/19
Train step:3/19
Train step:4/19
Train step:5/19
Train step:6/19
Train step:7/19
Train step:8/19
Train step:9/19
Train step:10/19
Train step:11/19
Train step:12/19
Train step:13/19
Train step:14/19
Train step:15/19
Train step:16/19
Train step:17/19
Train step:18/19
Valid step:0/4
Valid step:1/4
Valid step:2/4
Valid step:3/4
Epoch: 1,Loss:1.88785
Epoch: 1,Loss:0.41403
Epoch 2/19
Train step:0/19
Train step:1/19
Train step:2/19
Train step:3/19
Train step:4/19
Train step:5/19
Train step:6/19
Train step:7/19
Train

Train step:3/19
Train step:4/19
Train step:5/19
Train step:6/19
Train step:7/19
Train step:8/19
Train step:9/19
Train step:10/19
Train step:11/19
Train step:12/19
Train step:13/19
Train step:14/19
Train step:15/19
Train step:16/19
Train step:17/19
Train step:18/19
Valid step:0/4
Valid step:1/4
Valid step:2/4
Valid step:3/4
Epoch:19,Loss:1.18692
Epoch:19,Loss:0.38514


### Save your model
You can save your best model

In [26]:
torch.save(best_model, './air_model_frame.pth')

## Test
### Load your model
Next, we load our model for testing.

In [27]:
m1 = Net()
m1.load_state_dict(torch.load('./air_model_frame.pth'))
print(m1)

Net(
  (fc1): Linear(in_features=257, out_features=1024, bias=True)
  (fc2): Linear(in_features=1024, out_features=1024, bias=True)
  (fc3): Linear(in_features=1024, out_features=1024, bias=True)
  (fc4): Linear(in_features=1024, out_features=257, bias=True)
)


### Test with testing data
Feed your testing data to your model and get the result.

In [21]:
testData = data.DataLoader(testDataLoader()) 
for step, audio in enumerate(testData):
    print(step)
    name = teList[step]
    name = name.split('.')[0]
    name = name+'.wav'
    wavpath = './result_frame/'
    
    m1.eval()
    output = m1(audio)
    output = librosa.istft(np.transpose(output[0].cpu().data.numpy().squeeze()), hop_length=160,win_length=400) 
    librosa.output.write_wav(wavpath+name, output, 16000)
    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
